In [15]:
import polars as pl
import polars.selectors as cs
import os
import sys
from datetime import datetime, timezone
import plotly.express as px
import numpy as np

PROJECT_PATH = os.path.abspath(os.path.join("..", ".."))
PIPELINE_PATH = os.path.join(PROJECT_PATH, "pipeline")
DATA_DIRECTORY = os.path.join(PROJECT_PATH, "data")

if PIPELINE_PATH not in sys.path:
    sys.path.append(PIPELINE_PATH)
    
from utils.paths import PROCESSED_PICARRO_DATA_DIRECTORY, POSTPROCESSED_DATA_DIRECTORY

assert(os.path.exists(POSTPROCESSED_DATA_DIRECTORY))
assert(os.path.exists(PROCESSED_PICARRO_DATA_DIRECTORY))

In [81]:
# Filters 2024
ids = [10]

df = pl.read_parquet(os.path.join(DATA_DIRECTORY, "output", "side-by-side", "2024_L1_1_min_sbs_period_acropolis.parquet")) \
    .filter(pl.col("system_id").is_in(ids)) \
    .select("datetime", "system_id", "slope", "intercept") \
    .group_by_dynamic("datetime", every='1d', group_by=["system_id"]) \
    .agg(cs.numeric().last()) \
    .sort("datetime") \
    .with_columns(ordinal_day = pl.col("datetime").dt.ordinal_day()) \
    .with_row_index()
    
fig = px.scatter(df, x="datetime", y = "slope")
fig.show()

In [80]:
# Filters
ids = [6]

df = pl.read_parquet(os.path.join(DATA_DIRECTORY, "output", "side-by-side", "2025_L1_1_min_sbs_period_acropolis.parquet")) \
    .filter(pl.col("system_id").is_in(ids)) \
    .select("datetime", "system_id", "cal_gmp343_slope", "cal_gmp343_intercept") \
    .group_by_dynamic("datetime", every='1d', group_by=["system_id"]) \
    .agg(cs.numeric().last()) \
    .sort("datetime") \
    .with_columns(ordinal_day = pl.col("datetime").dt.ordinal_day()) \
    .with_row_index()
    
fig = px.scatter(df, x="datetime", y = "cal_gmp343_slope")
fig.show()

In [69]:
df

shape: (46, 6)
┌───────┬───────────┬─────────────────────┬──────────────────┬──────────────────────┬─────────────┐
│ index ┆ system_id ┆ datetime            ┆ cal_gmp343_slope ┆ cal_gmp343_intercept ┆ ordinal_day │
│ ---   ┆ ---       ┆ ---                 ┆ ---              ┆ ---                  ┆ ---         │
│ u32   ┆ i32       ┆ datetime[ms]        ┆ f64              ┆ f64                  ┆ i16         │
╞═══════╪═══════════╪═════════════════════╪══════════════════╪══════════════════════╪═════════════╡
│ 0     ┆ 3         ┆ 2025-02-22 00:00:00 ┆ null             ┆ null                 ┆ 53          │
│ 1     ┆ 3         ┆ 2025-04-11 00:00:00 ┆ 0.9911           ┆ -17.48               ┆ 101         │
│ 2     ┆ 6         ┆ 2025-04-05 00:00:00 ┆ 1.0392           ┆ -2.24                ┆ 95          │
│ 3     ┆ 6         ┆ 2025-03-28 00:00:00 ┆ 1.0419           ┆ -3.82                ┆ 87          │
│ 4     ┆ 6         ┆ 2025-02-18 00:00:00 ┆ 1.03             ┆ 1.39                 ┆ 49          │
│ …     ┆ …         ┆ …                   ┆ …                ┆ …                    ┆ …           │
│ 41    ┆ 6         ┆ 2025-04-23 00:00:00 ┆ 1.0338           ┆ 0.07                 ┆ 113         │
│ 42    ┆ 6         ┆ 2025-04-03 00:00:00 ┆ 1.0311           ┆ 0.81                 ┆ 93          │
│ 43    ┆ 6         ┆ 2025-02-28 00:00:00 ┆ 1.0356           ┆ -1.56                ┆ 59          │
│ 44    ┆ 6         ┆ 2025-05-10 00:00:00 ┆ 1.0275           ┆ -1.92                ┆ 130         │
│ 45    ┆ 3         ┆ 2025-02-28 00:00:00 ┆ 0.9862           ┆ -18.45               ┆ 59          │
└───────┴───────────┴─────────────────────┴──────────────────┴──────────────────────┴─────────────┘

In [8]:
# Filters
start_date = datetime(2025, 2, 18, 0, 0, 0)
end_date = datetime(2025, 5, 31, 0, 0, 0)

filter = '1h'
ids = [3,6]

In [9]:
# Load Picarro Data
# DWD Picarro: "Calibrated_1_min_DWD_Picarro_G2301_413.parquet"
df_p_dwd = pl.scan_parquet(os.path.join(PROCESSED_PICARRO_DATA_DIRECTORY,"Calibrated_1_min_DWD_Picarro_G2301_413.parquet"))
df_p_dwd = df_p_dwd.filter(pl.col("datetime").is_between(start_date, end_date)).collect()

# ICOS Picarro: "Calibrated_1_min_ICOS_Picarro_G2401_529.parquet"
df_p_icos = pl.scan_parquet(os.path.join(PROCESSED_PICARRO_DATA_DIRECTORY,"Calibrated_1_min_ICOS_Picarro_G2401_529.parquet"))
df_p_icos = df_p_icos.filter(pl.col("datetime").is_between(start_date, end_date)).collect()
    
df_p = pl.concat([df_p_dwd,df_p_icos], how="diagonal")
del df_p_dwd, df_p_icos
df_p.head(1).vstack(df_p.tail(1))

shape: (2, 5)
┌─────────────────────┬───────────────┬───────────┬───────────────────┬──────────────┐
│ datetime            ┆ system_name   ┆ system_id ┆ picarro_corrected ┆ h2o_reported │
│ ---                 ┆ ---           ┆ ---       ┆ ---               ┆ ---          │
│ datetime[ms]        ┆ str           ┆ i32       ┆ f64               ┆ f64          │
╞═════════════════════╪═══════════════╪═══════════╪═══════════════════╪══════════════╡
│ 2025-02-18 00:00:00 ┆ Picarro_G2401 ┆ 529       ┆ 470.619119        ┆ 0.503802     │
│ 2025-05-31 00:00:00 ┆ Picarro_G2401 ┆ 529       ┆ 478.524646        ┆ 1.737918     │
└─────────────────────┴───────────────┴───────────┴───────────────────┴──────────────┘

In [10]:
df = pl.read_parquet(os.path.join(DATA_DIRECTORY, "output", "side-by-side", "2025_L1_1_min_sbs_period_acropolis.parquet")) \
    .with_columns(ordinal_day = pl.col("datetime").dt.ordinal_day()).filter(pl.col("datetime").is_between(start_date, end_date))
df.head(1).vstack(df.tail(1))

shape: (2, 19)
┌────────────┬───────────┬────────────┬────────────┬───┬──────┬────────────┬───────────┬───────────┐
│ datetime   ┆ system_id ┆ system_nam ┆ gmp343_cor ┆ … ┆ Flag ┆ picarro_co ┆ Picarro_F ┆ ordinal_d │
│ ---        ┆ ---       ┆ e          ┆ rected     ┆   ┆ ---  ┆ rrected    ┆ lag       ┆ ay        │
│ datetime[m ┆ i32       ┆ ---        ┆ ---        ┆   ┆ str  ┆ ---        ┆ ---       ┆ ---       │
│ s]         ┆           ┆ str        ┆ f64        ┆   ┆      ┆ f64        ┆ str       ┆ i16       │
╞════════════╪═══════════╪════════════╪════════════╪═══╪══════╪════════════╪═══════════╪═══════════╡
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 470.18     ┆ … ┆ U    ┆ 470.62     ┆ U         ┆ 49        │
│ 00:00:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-05-31 ┆ 6         ┆ acropolis- ┆ 480.77     ┆ … ┆ U    ┆ 478.52     ┆ U         ┆ 151       │
│ 00:00:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
└────────────┴───────────┴────────────┴────────────┴───┴──────┴────────────┴───────────┴───────────┘

In [5]:
fig = px.line(df.filter(pl.col("system_id") == 3), x="datetime", y = "gmp343_corrected", color = "system_id")
fig.show()

In [64]:
def reduce_calibration_days(df, frequency_days):
    df_cal = df.filter(pl.col("ordinal_day")%frequency_days == 0) \
        .select("datetime", "system_id", "slope_interpolated", "intercept_interpolated") \
        .group_by_dynamic("datetime", every='1d', group_by=["system_id"]) \
        .agg(cs.numeric().mean()) \
        .sort("datetime")
                
    return df.select("datetime", "system_id", "gmp343_dry") \
        .sort("datetime") \
        .join(df_cal, on=["datetime", "system_id"], how="left") \
        .sort(["system_id", "datetime"]) \
        .group_by("system_id").agg([
        pl.col("datetime"),
        pl.col("gmp343_dry"),
        pl.col("slope_interpolated").interpolate().backward_fill().forward_fill(),
        pl.col("intercept_interpolated").interpolate().backward_fill().forward_fill()
        ]) \
        .explode(["datetime","gmp343_dry", "slope_interpolated", "intercept_interpolated"]) \
        .with_columns(((pl.col("gmp343_dry")) * pl.col("slope_interpolated") + pl.col("intercept_interpolated")).alias(f"gmp343_corrected")) \
        .join(df_p.select("datetime", "picarro_corrected"), on="datetime") \
        .with_columns(diff = pl.col("gmp343_corrected") - pl.col("picarro_corrected")) \
        .filter(pl.col("diff").is_not_nan()) \
        .group_by_dynamic("datetime", every='1h', group_by=["system_id"]) \
        .agg(cs.numeric().mean()) \
        .group_by("system_id") \
        .agg((pl.col("diff").pow(2).mean().sqrt()).alias(f"rmse_{frequency_days}days"))


In [65]:
df_plot = reduce_calibration_days(df, 2)

for frequency_days in [3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20]:
    df_plot = df_plot.join(reduce_calibration_days(df, frequency_days), on="system_id", how="left")

df_plot = df_plot.drop("^.*_right$").with_columns(
    pl.concat_str([pl.lit("MidCost-"),pl.col("system_id").cast(pl.Utf8)], separator="")
    .alias("system_name")
)
df_plot

shape: (2, 21)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ system_id ┆ rmse_2day ┆ rmse_3day ┆ rmse_4day ┆ … ┆ rmse_18da ┆ rmse_19da ┆ rmse_20da ┆ system_n │
│ ---       ┆ s         ┆ s         ┆ s         ┆   ┆ ys        ┆ ys        ┆ ys        ┆ ame      │
│ i32       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆ f64       ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ str      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 3         ┆ 0.625746  ┆ 0.622111  ┆ 0.598867  ┆ … ┆ 0.66924   ┆ 0.826221  ┆ 0.919888  ┆ MidCost- │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 3        │
│ 6         ┆ 0.939251  ┆ 0.935474  ┆ 0.967721  ┆ … ┆ 1.141812  ┆ 1.226322  ┆ 1.136927  ┆ MidCost- │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 6        │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [66]:
for id in ids:
    list = df_plot.filter(pl.col("system_id") == id).drop(["system_name", "system_id"]).transpose().get_column("column_0")

    fig = px.line(x = range(2,len(list)+2), y = list)
    fig.show()

In [6]:
df

shape: (254_412, 19)
┌────────────┬───────────┬────────────┬────────────┬───┬──────┬────────────┬───────────┬───────────┐
│ datetime   ┆ system_id ┆ system_nam ┆ gmp343_cor ┆ … ┆ Flag ┆ picarro_co ┆ Picarro_F ┆ ordinal_d │
│ ---        ┆ ---       ┆ e          ┆ rected     ┆   ┆ ---  ┆ rrected    ┆ lag       ┆ ay        │
│ datetime[m ┆ i32       ┆ ---        ┆ ---        ┆   ┆ str  ┆ ---        ┆ ---       ┆ ---       │
│ s]         ┆           ┆ str        ┆ f64        ┆   ┆      ┆ f64        ┆ str       ┆ i16       │
╞════════════╪═══════════╪════════════╪════════════╪═══╪══════╪════════════╪═══════════╪═══════════╡
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 470.18     ┆ … ┆ U    ┆ 470.62     ┆ U         ┆ 49        │
│ 00:00:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 466.63     ┆ … ┆ U    ┆ 467.38     ┆ U         ┆ 49        │
│ 00:01:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 458.89     ┆ … ┆ U    ┆ 462.71     ┆ U         ┆ 49        │
│ 00:02:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 458.46     ┆ … ┆ U    ┆ 459.32     ┆ U         ┆ 49        │
│ 00:03:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-02-18 ┆ 3         ┆ acropolis- ┆ 464.85     ┆ … ┆ U    ┆ 464.31     ┆ U         ┆ 49        │
│ 00:04:00   ┆           ┆ 3          ┆            ┆   ┆      ┆            ┆           ┆           │
│ …          ┆ …         ┆ …          ┆ …          ┆ … ┆ …    ┆ …          ┆ …         ┆ …         │
│ 2025-05-30 ┆ 6         ┆ acropolis- ┆ 480.96     ┆ … ┆ U    ┆ 477.92     ┆ U         ┆ 150       │
│ 23:56:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-05-30 ┆ 6         ┆ acropolis- ┆ 478.64     ┆ … ┆ U    ┆ 477.97     ┆ U         ┆ 150       │
│ 23:57:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-05-30 ┆ 6         ┆ acropolis- ┆ 480.88     ┆ … ┆ U    ┆ 478.19     ┆ U         ┆ 150       │
│ 23:58:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-05-30 ┆ 6         ┆ acropolis- ┆ 480.59     ┆ … ┆ U    ┆ 478.76     ┆ U         ┆ 150       │
│ 23:59:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
│ 2025-05-31 ┆ 6         ┆ acropolis- ┆ 480.77     ┆ … ┆ U    ┆ 478.52     ┆ U         ┆ 151       │
│ 00:00:00   ┆           ┆ 6          ┆            ┆   ┆      ┆            ┆           ┆           │
└────────────┴───────────┴────────────┴────────────┴───┴──────┴────────────┴───────────┴───────────┘

In [ ]:
from typing import List

def create_list_of_calibration_days(df, frequency_days:int) -> List[List[int]]:
    1+y, 1+y+frequency_days*n
    
    return [[0], ]


def reduce_calibration_days(df, selected_days):
    # Filter the dataframe to only include the selected days
    df_cal = df.filter(pl.col("ordinal_day").is_in(selected_days)) \
        .select("datetime", "system_id", "cal_gmp343_slope", "cal_gmp343_intercept") \
        .group_by_dynamic("datetime", every='1d', group_by=["system_id"]) \
        .agg(cs.numeric().last()) \
        .sort("datetime")
                
                
                
                
    return df.select("datetime", "system_id", "gmp343_dry") \
        .sort("datetime") \
        .join(df_cal, on=["datetime", "system_id"], how="left") \
        .sort(["system_id", "datetime"]) \
        .group_by("system_id").agg([
        pl.col("datetime"),
        pl.col("gmp343_dry"),
        pl.col("slope_interpolated").interpolate().backward_fill().forward_fill(),
        pl.col("intercept_interpolated").interpolate().backward_fill().forward_fill()
        ]) \
        .explode(["datetime","gmp343_dry", "slope_interpolated", "intercept_interpolated"]) \
        .with_columns(((pl.col("gmp343_dry")) * pl.col("slope_interpolated") + pl.col("intercept_interpolated")).alias(f"gmp343_corrected")) \
        .join(df_p.select("datetime", "picarro_corrected"), on="datetime") \
        .with_columns(diff = pl.col("gmp343_corrected") - pl.col("picarro_corrected")) \
        .filter(pl.col("diff").is_not_nan()) \
        .group_by_dynamic("datetime", every='1h', group_by=["system_id"]) \
        .agg(cs.numeric().mean()) \
        .group_by("system_id") \
        .agg((pl.col("diff").pow(2).mean().sqrt()).alias(f"rmse_{frequency_days}days"))
